In [16]:
import cv2
import numpy as np

from PIL import Image
from transparent_background import Remover
import pandas as pd
from tqdm import tqdm
import os

In [5]:
# Load model
# remover = Remover() # default setting
# remover = Remover(mode='fast', jit=True, device='cuda:0', ckpt='~/latest.pth', url="https://drive.google.com/file/d/13oBl5MTVcWER3YU4fSxW3ATlVfueFQPY/view?usp=share_link", ckpt_name="ckpt_base.pth")
remover = Remover(mode="base-nightly")  # nightly release checkpoint

Settings -> Mode=base-nightly, Device=cuda:0, Torchscript=disabled


In [7]:
# Usage for image
img = Image.open("../data/raw/images/egyptian/1953/1953.1-tt.jpg").convert("RGB")  # read image

out = remover.process(img)  # default setting - transparent background
# out = remover.process(img, type='rgba') # same as above
# out = remover.process(img, type='map') # object map only
# out = remover.process(img, type='green') # image matting - green screen
# out = remover.process(img, type='white')  # change backround with white color
# out = remover.process(img, type=[255, 0, 0]) # change background with color code [255, 0, 0]
# out = remover.process(img, type='blur') # blur background
# out = remover.process(img, type='overlay') # overlay object map onto the image
# out = remover.process(img, type='samples/background.jpg') # use another image as a background

# out = remover.process(img, threshold=0.5) # use threhold parameter for hard prediction.

out.save("output.png")  # save result

In [24]:
img_df = pd.read_csv("../data/processed/OM_file_to_obj.csv")
img_df["full_path"] = img_df.apply(lambda row: os.path.join(row["root"], row["file"]), axis=1)
img_df["new_root"] = img_df["root"].apply(
    lambda x: x.replace("data/raw/images/", "data/processed/OM_images_white/")
)
img_df["new_full_path"] = img_df.apply(lambda row: os.path.join(row["new_root"], row["file"]), axis=1)

In [23]:
img_df

file                               root  \
0           1985.15.68.jpg  data/raw/images/fulling_mill/1985   
1       1985.52.37.ff2.jpg  data/raw/images/fulling_mill/1985   
2      1985.81.4496 d2.jpg  data/raw/images/fulling_mill/1985   
3        1985.9.1.1-d4.jpg  data/raw/images/fulling_mill/1985   
4       1985.52.37.sf2.jpg  data/raw/images/fulling_mill/1985   
...                    ...                                ...   
39239      2014.1.2 bb.jpg      data/raw/images/egyptian/2014   
39240     2014.1.71 ll.jpg      data/raw/images/egyptian/2014   
39241      2014.1.2 rr.jpg      data/raw/images/egyptian/2014   
39242           1963.4.jpg      data/raw/images/egyptian/1963   
39243         1963.4.2.jpg      data/raw/images/egyptian/1963   

                  obj_num                                          full_path  \
0        durma.1985.15.68   data/raw/images/fulling_mill/1985/1985.15.68.jpg   
1        durma.1985.52.37  data/raw/images/fulling_mill/1985/1985.52.37.f...   
2      durma.1985.81.4496  data/raw/images/fulling_mill/1985/1985.81.4496...   
3          durma.1985.9.1  data/raw/images/fulling_mill/1985/1985.9.1.1-d...   
4        durma.1985.52.37  data/raw/images/fulling_mill/1985/1985.52.37.s...   
...                   ...                                                ...   
39239      durom.2014.1.2      data/raw/images/egyptian/2014/2014.1.2 bb.jpg   
39240     durom.2014.1.71     data/raw/images/egyptian/2014/2014.1.71 ll.jpg   
39241      durom.2014.1.2      data/raw/images/egyptian/2014/2014.1.2 rr.jpg   
39242        durom.1963.4           data/raw/images/egyptian/1963/1963.4.jpg   
39243        durom.1963.4         data/raw/images/egyptian/1963/1963.4.2.jpg   

                                               new_root  
0      data/processed/OM_images_white/fulling_mill/1985  
1      data/processed/OM_images_white/fulling_mill/1985  
2      data/processed/OM_images_white/fulling_mill/1985  
3      data/processed/OM_images_white/fulling_mill/1985  
4      data/processed/OM_images_white/fulling_mill/1985  
...                                                 ...  
39239      data/processed/OM_images_white/egyptian/2014  
39240      data/processed/OM_images_white/egyptian/2014  
39241      data/processed/OM_images_white/egyptian/2014  
39242      data/processed/OM_images_white/egyptian/1963  
39243      data/processed/OM_images_white/egyptian/1963  

[39244 rows x 5 columns]

In [26]:
for index, row in tqdm(img_df.iterrows(), total=img_df.shape[0]):
    img = Image.open('../' + row['full_path']).convert('RGB')  # read image
    out = remover.process(img, type='white')  # change backround with white color
    # make sure the directory exists
    os.makedirs('../' + row['new_root'], exist_ok=True)
    out.save('../' + row['new_full_path'])  # save result

  0%|          | 84/39244 [00:06<52:59, 12.32it/s] 


KeyboardInterrupt: 